In [0]:
from pyspark.sql import functions as F

# 1. Configuración
CATALOGO       = "santig_120781"
ESQUEMA_SILVER = f"{CATALOGO}.silver"
ESQUEMA_GOLD   = f"{CATALOGO}.gold"

print("--- Iniciando Generación de Capa Gold (Maestra de Ventas) ---")

# 2. Carga de tablas (Vienen de la Silver ya unificada)
df_orders         = spark.read.table(f"{ESQUEMA_SILVER}.orders")
df_products       = spark.read.table(f"{ESQUEMA_SILVER}.products")
df_aisles         = spark.read.table(f"{ESQUEMA_SILVER}.aisles")
df_departments    = spark.read.table(f"{ESQUEMA_SILVER}.departments")
df_products_prior = spark.read.table(f"{ESQUEMA_SILVER}.order_products__prior")
df_products_train = spark.read.table(f"{ESQUEMA_SILVER}.order_products__train")

# 3. Unión de detalles (Prior + Train)
df_all_details = df_products_prior.unionByName(df_products_train, allowMissingColumns=True)

# 4. Construcción de la Tabla Maestra (JOINS)
# Usamos Inner Join para órdenes porque necesitamos que tengan detalle, 
# y Left para dimensiones para no perder registros si falta un producto.
df_master = df_all_details \
    .join(df_orders, "order_id", "inner") \
    .join(df_products, "product_id", "left") \
    .join(df_aisles, "aisle_id", "left") \
    .join(df_departments, "department_id", "left")

# 5. Transformaciones de Negocio y Limpieza
df_gold = df_master.withColumn(
    "department", 
    F.coalesce(F.col("department"), F.lit("Missing/Other"))
).withColumn(
    "aisle", 
    F.coalesce(F.col("aisle"), F.lit("Missing/Other"))
).withColumn(
    "day_type", 
    F.when(F.col("order_dow").isin(0, 6), "Weekend").otherwise("Weekday")
).withColumn(
    "time_segment",
    F.when((F.col("order_hour_of_day") >= 6) & (F.col("order_hour_of_day") < 12), "Morning")
     .when((F.col("order_hour_of_day") >= 12) & (F.col("order_hour_of_day") < 18), "Afternoon")
     .when((F.col("order_hour_of_day") >= 18) & (F.col("order_hour_of_day") < 24), "Evening")
     .otherwise("Night")
)

# 6. Selección Final de Columnas para el Dashboard
df_final = df_gold.select(
    "order_id", 
    "order_date", 
    "user_id", 
    "day_type", 
    "time_segment",
    "order_hour_of_day", 
    "product_name", 
    "aisle", 
    "department", 
    "add_to_cart_order",
    "reordered"
).dropDuplicates() # Seguridad ante duplicados en los joins

# 7. Guardado en Gold
df_final.write.format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable(f"{ESQUEMA_GOLD}.master_sales_report")

# 8. OPTIMIZACIÓN (Z-ORDER)
# Esto hace que filtrar por fecha o departamento sea súper rápido
spark.sql(f"OPTIMIZE {ESQUEMA_GOLD}.master_sales_report ZORDER BY (order_date, department)")

print(f"Capa Gold finalizada. Total registros: {df_final.count()}")

--- Iniciando Generación de Capa Gold (Maestra de Ventas) ---
✅ Capa Gold finalizada. Total registros: 105400


In [0]:
%sql
select * from santig_120781.gold.master_sales_report

order_id order_date user_id day_type time_segment order_hour_of_day product_name aisle department add_to_cart_order reordered 6 2023-10-30 22352 Weekday Afternoon 12 Cleanse refrigerated beverages 1 0 6 2023-10-30 22352 Weekday Afternoon 12 Dryer Sheets Geranium Scent laundry household 2 0 6 2023-10-30 22352 Weekday Afternoon 12 Clean Day Lavender Scent Room Freshener Spray air fresheners candles household 3 0 8 2023-11-08 3107 Weekday Morning 6 Original Hawaiian Sweet Rolls buns rolls bakery 1 1 13 2023-12-31 45082 Weekend Afternoon 17 Light beers coolers alcohol 1 0 13 2023-12-31 45082 Weekend Afternoon 17 Chunky Salsa Medium preserved dips spreads pantry 2 0 13 2023-12-31 45082 Weekend Afternoon 17 Handmade Vodka From Austin, Texas spirits alcohol 3 0 13 2023-12-31 45082 Weekend Afternoon 17 Soda soft drinks beverages 4 0 13 2023-12-31 45082 Weekend Afternoon 17 Salsa Con Queso Medium Dip preserved dips spreads pantry 5 0 13 2023-12-31 45082 Weekend Afternoon 17 G Series Lime Cucumber Sports Drink energy sports drinks beverages 6 0 13 2023-12-31 45082 Weekend Afternoon 17 Lemon Lime Thirst Quencher energy sports drinks beverages 7 0 13 2023-12-31 45082 Weekend Afternoon 17 Lemonade refrigerated beverages 8 0 13 2023-12-31 45082 Weekend Afternoon 17 Sparkling Natural Mineral Water water seltzer sparkling water beverages 9 0 13 2023-12-31 45082 Weekend Afternoon 17 Diet Tonic Water soft drinks beverages 10 0 13 2023-12-31 45082 Weekend Afternoon 17 Philadelphia Original Cream Cheese other creams cheeses dairy eggs 11 0 13 2023-12-31 45082 Weekend Afternoon 17 Hampshire 100% Natural Sour Cream other creams cheeses dairy eggs 12 0 13 2023-12-31 45082 Weekend Afternoon 17 Original Potato Chips chips pretzels snacks 13 0 14 2023-01-26 18194 Weekday Afternoon 15 Hair Bender Whole Bean Coffee coffee beverages 1 1 14 2023-01-26 18194 Weekday Afternoon 15 Organic Whole Milk milk dairy eggs 2 1 14 2023-01-26 18194 Weekday Afternoon 15 Organic Mini Homestyle Waffles frozen breakfast frozen 3 1 14 2023-01-26 18194 Weekday Afternoon 15 Naturals Chicken Nuggets frozen appetizers sides frozen 4 1 14 2023-01-26 18194 Weekday Afternoon 15 Unprocessed American Singles Colby-Style Cheese packaged cheese dairy eggs 5 1 14 2023-01-26 18194 Weekday Afternoon 15 Organic Mesa Sunrise Cereal cereal breakfast 6 1 14 2023-01-26 18194 Weekday Afternoon 15 Total Greek Strained Yogurt yogurt dairy eggs 7 1 14 2023-01-26 18194 Weekday Afternoon 15 Corn Meal Pizza Crust frozen breads doughs frozen 8 1 14 2023-01-26 18194 Weekday Afternoon 15 Sriracha Chili Sauce asian foods international 9 0 14 2023-01-26 18194 Weekday Afternoon 15 Organic Broccoli Florets frozen produce frozen 10 1 14 2023-01-26 18194 Weekday Afternoon 15 Honeycrisp Apple fresh fruits produce 11 0 15 2023-08-02 54901 Weekday Morning 11 Spring Water water seltzer sparkling water beverages 1 1 15 2023-08-02 54901 Weekday Morning 11 Organic Extra Virgin Olive Oil oils vinegars pantry 2 1 15 2023-08-02 54901 Weekday Morning 11 Pinto Beans No Salt Added canned meals beans canned goods 3 1 15 2023-08-02 54901 Weekday Morning 11 Honeysuckle Hand Soap soap personal care 4 1 15 2023-08-02 54901 Weekday Morning 11 Olive Oil & Aloe Vera Hand Soap soap personal care 5 1 22 2023-04-02 30822 Weekday Morning 8 2% Reduced Fat Milk milk dairy eggs 1 1 22 2023-04-02 30822 Weekday Morning 8 Butter Top White Bread bread bakery 2 1 22 2023-04-02 30822 Weekday Morning 8 Banana fresh fruits produce 3 1 22 2023-04-02 30822 Weekday Morning 8 Iceberg Lettuce fresh vegetables produce 4 1 22 2023-04-02 30822 Weekday Morning 8 Broccoli Florets packaged vegetables fruits produce 5 1 22 2023-04-02 30822 Weekday Morning 8 Large Grade AA Eggs eggs dairy eggs 6 1 22 2023-04-02 30822 Weekday Morning 8 Provolone Slices packaged cheese dairy eggs 7 1 22 2023-04-02 30822 Weekday Morning 8 Vine Ripe Tomatoes fresh vegetables produce 8 0 22 2023-04-02 30822 Weekday Morning 8 Boneless And Skinless Chicken Breast poultry counter 

VALIDACION DE DATOS

In [0]:
from pyspark.sql import functions as F

# Configuración
GOLD_TABLE = "santig_120781.gold.master_sales_report"
df_gold = spark.read.table(GOLD_TABLE)

print(f"--- Iniciando Auditoría de {GOLD_TABLE} ---")

# 1. PRUEBA DE VOLUMEN (¿Perdimos datos en los JOINS?)
# El total debería ser igual a la suma de order_products_prior + train
total_rows = df_gold.count()
print(f"1. Total de registros en Gold: {total_rows:,}")



--- Iniciando Auditoría de santig_120781.gold.master_sales_report ---
1. Total de registros en Gold: 638,592


In [0]:
# 2. PRUEBA DE CALIDAD (¿Hay nulos críticos?)
# Si los Joins fallaron, verás nulos en nombres de productos o departamentos
null_analysis = df_gold.select([
    F.count(F.when(F.col(c).isNull(), c)).alias(c) 
    for c in ["product_name", "department", "order_date"]
])
print("\n2. Análisis de Nulos (debería ser 0):")
display(null_analysis)



2. Análisis de Nulos (debería ser 0):


product_name department order_date 0 0 0

In [0]:
# Ver los productos que están causando los nulos en departamento
display(df_gold.filter(F.col("department").isNull()).select("product_name").distinct())

product_name

In [0]:
# 3. VERIFICACIÓN DE REGLAS DE NEGOCIO (Segmentos de tiempo)
# Verificamos que 'time_segment' y 'day_type' se llenaron correctamente
print("\n3. Distribución de Segmentos de Tiempo:")
df_gold.groupBy("time_segment").count().show()

print("Distribución por Tipo de Día:")
df_gold.groupBy("day_type").count().show()



3. Distribución de Segmentos de Tiempo:
+------------+------+
|time_segment| count|
+------------+------+
|     Evening|113821|
|     Morning|206630|
|   Afternoon|306310|
|       Night| 11831|
+------------+------+

Distribución por Tipo de Día:
+--------+------+
|day_type| count|
+--------+------+
| Weekday|409910|
| Weekend|228682|
+--------+------+



In [0]:
# 4. PRUEBA DE INTEGRIDAD TEMPORAL
# Verificamos el rango de fechas para asegurar que la simulación funcionó
date_range = df_gold.select(
    F.min("order_date").alias("Fecha_Mas_Antigua"),
    F.max("order_date").alias("Fecha_Mas_Reciente")
)
print("\n4. Rango de Fechas en el Dataset:")
display(date_range)


4. Rango de Fechas en el Dataset:


Fecha_Mas_Antigua Fecha_Mas_Reciente 2023-01-01 2024-01-01

In [0]:
# 5. MUESTRA DE DATOS PARA POWER BI
# Simulamos lo que vería un usuario final
print("\n5. Muestra final de la Tabla Maestra:")
display(df_gold.select(
    "order_id", "order_date", "day_type", "product_name", "department"
).limit(10))


5. Muestra final de la Tabla Maestra:


order_id order_date day_type product_name department 6 2023-10-30 Weekday Cleanse beverages 6 2023-10-30 Weekday Dryer Sheets Geranium Scent household 6 2023-10-30 Weekday Clean Day Lavender Scent Room Freshener Spray household 8 2023-11-08 Weekday Original Hawaiian Sweet Rolls bakery 13 2023-12-31 Weekend Light alcohol 13 2023-12-31 Weekend Chunky Salsa Medium pantry 13 2023-12-31 Weekend Handmade Vodka From Austin, Texas alcohol 13 2023-12-31 Weekend Soda beverages 13 2023-12-31 Weekend Salsa Con Queso Medium Dip pantry 13 2023-12-31 Weekend G Series Lime Cucumber Sports Drink beverages

In [0]:
# 1. Cuantos registros hay en la union de los detalles (antes del Join)?
print(f"Detalles totales: {df_all_details.count()}")

# 2. Cuantos registros hay en la tabla de ordenes?
print(f"Ordenes totales: {df_orders.count()}")

# 3. Hay registros en detalles que NO tienen una orden correspondiente?
orphans = df_all_details.join(df_orders, "order_id", "left_anti").count()
print(f"Registros huerfanos (sin orden): {orphans}")

Detalles totales: 2097150
Órdenes totales: 1048575
Registros huérfanos (sin orden): 1458558


In [0]:
# Ver los IDs de ordenes que estan en productos pero NO en la tabla orders
df_missing_orders = df_all_details.join(df_orders, "order_id", "left_anti")

print("IDs de ordenes que estan en productos pero NO en la tabla orders:")
display(df_missing_orders.select("order_id").distinct().limit(10))

IDs de órdenes que están en productos pero NO en la tabla orders:


order_id 12 16 3 5 9 4 7 10 11 2

In [0]:
# Optimizamos la tabla física para Power BI
spark.sql(f"OPTIMIZE {ESQUEMA_GOLD}.master_sales_report ZORDER BY (order_date, department)")

print("Tabla Gold optimizada físicamente con Z-ORDER por Fecha y Departamento.")

🚀 Tabla Gold optimizada físicamente con Z-ORDER por Fecha y Departamento.


In [0]:
# Creamos una vista limpia para el reporte
spark.sql(f"""
CREATE OR REPLACE VIEW {ESQUEMA_GOLD}.vw_dashboard_ventas AS
SELECT 
    order_id,
    order_date,
    day_type,
    time_segment,
    product_name,
    aisle,
    department,
    add_to_cart_order,
    reordered,
    -- Agregamos un contador simple para facilitar cálculos en Power BI
    1 as cantidad_unidades 
FROM {ESQUEMA_GOLD}.master_sales_report
""")

print("Vista 'vw_dashboard_ventas' creada. Esta es la que debes importar en Power BI.")

📊 Vista 'vw_dashboard_ventas' creada. Esta es la que debes importar en Power BI.
